### Target(Total Bill) Analysis with Mutate Variable(tip rate)

In [2]:
import numpy as np
from sklearn.impute import SimpleImputer
import pymysql.cursors
import pandas as pd
import numpy as np
import pandas_profiling

connection = pymysql.connect(host='localhost',
        user='root',
        password='1234',
        db='tip',
        charset='utf8',
        cursorclass=pymysql.cursors.DictCursor)

try:
    with connection.cursor() as cursor:
        # Read a single record (sql)
        sql = "SELECT * FROM tips;"
        cursor.execute(sql) # cursor 실행
        result = cursor.fetchall()
        df = pd.DataFrame(result) # dateframe에 result 저장
finally:
    connection.close()

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  250 non-null    float64
 1   tip         248 non-null    float64
 2   sex         250 non-null    object 
 3   smoker      250 non-null    object 
 4   day         250 non-null    object 
 5   time        249 non-null    object 
 6   size        248 non-null    float64
dtypes: float64(3), object(4)
memory usage: 13.8+ KB


In [4]:
df['sex'].replace({'Female':0,'Male':1}, inplace=True)
df['smoker'].replace({'No':0,'Yes':1},inplace=True)
df['day'].replace({'Thur':0,'Fri':1,'Sat':2,'Sun':3},inplace=True)
df['time'].replace({'Lunch':0, 'Dinner':1},inplace=True)
df['tip_rate'] = (df['tip'] / df['total_bill'] * 100).round(2)

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  250 non-null    float64
 1   tip         248 non-null    float64
 2   sex         250 non-null    int64  
 3   smoker      250 non-null    int64  
 4   day         250 non-null    object 
 5   time        249 non-null    float64
 6   size        248 non-null    float64
 7   tip_rate    248 non-null    float64
dtypes: float64(5), int64(2), object(1)
memory usage: 15.8+ KB


In [6]:
df.isnull().sum()

total_bill    0
tip           2
sex           0
smoker        0
day           0
time          1
size          2
tip_rate      2
dtype: int64

In [7]:
df.replace('',np.nan,inplace=True)

In [8]:
# SimpleImputer클래스로 median값으로 변경
imputer = SimpleImputer(strategy='median')

imputer.fit(df)

data_xtrans = imputer.transform(df)

data_xtrans = pd.DataFrame(data_xtrans,columns=df.columns)

In [9]:
data_xtrans.isnull().sum()

total_bill    0
tip           0
sex           0
smoker        0
day           0
time          0
size          0
tip_rate      0
dtype: int64

In [10]:
x = data_xtrans.drop('total_bill',axis=1) # 독립변수 
y = data_xtrans['total_bill'] # 목표변수 => 'total_bill'

In [13]:
x.profile_report()

Summarize dataset:   0%|          | 0/20 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [11]:
data= x.values

## * 이상치 발견 및 제거과정
- z-score는 해당 데이터가 평균으로부터 얼마나 멀리 떨어져 있는지, 그 떨어진 정도가 표준편차의 몇배인지를 나타낸다.
- z-score의 값이 아주 클수록 평균에서는 아주 먼 값이며, 표준편차보다는 큰 값을 의미한다.
- 즉, <u>**이상치**</u>이다.
- 표준화된 z-score값을 통해 잘못된 이상치를 파악할 수 있으며, 통상적으로 z-score의 절대값이 2가 넘는 경우 이를 이상치라 정의한다.

## Feature Scaling **(정규화)**
- **반드시 이상치 제거 과정을 거친 후 정규화 작업을 해야한다**



In [12]:
from sklearn.preprocessing import MinMaxScaler

trans = MinMaxScaler()

data_norm = trans.fit_transform(data)

xdata_norm = pd.DataFrame(data_norm,columns=x.columns,index = x.index)

xdata_norm.profile_report()

Summarize dataset:   0%|          | 0/20 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [85]:
from sklearn.decomposition import PCA

# define the transform
trans = PCA(n_components=3)

# transform the data
x_dim = trans.fit_transform(data_norm)
print(trans.explained_variance_ratio_)
print(sum(trans.explained_variance_ratio_))


[0.40049136 0.26816142 0.23312374]
0.9017765207722724


In [79]:
from sklearn.feature_selection import RFE
from sklearn.svm import SVR

estimator = SVR(kernel="linear")

# define RFE
rfe = RFE(estimator, n_features_to_select=3)
rfe.fit_transform(xdata_norm,y)
rfe.support_

array([ True, False, False, False, False,  True,  True])

In [81]:
RFE_featurn_3 = [i[1] for i in list(zip(rfe.support_,x.columns)) if i[0] ]
RFE_featurn_3

['tip', 'size', 'tip_rate']

In [83]:
RFE_featurn_3.append('total_bill')
RFE_col = []
for column in list(df.columns):
    if column not in RFE_featurn_3:
        RFE_col.append(column)
RFE = df.drop(RFE_col, axis=1)

In [84]:
RFE.profile_report()

Summarize dataset:   0%|          | 0/17 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [86]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_regression

fs = SelectKBest(score_func=f_regression, k=3)

X_selected = fs.fit_transform(data_norm, y)
fs.get_support()

array([ True, False, False, False, False,  True,  True])

In [87]:
RFS_featurn_3 = [i[1] for i in list(zip(fs.get_support(),x.columns)) if i[0] ]
RFS_featurn_3

['tip', 'size', 'tip_rate']

In [88]:
RFS_featurn_3.append('total_bill')
RFS_col = []
for column in list(df.columns):
    if column not in RFS_featurn_3:
        RFS_col.append(column)
RFS = df.drop(RFS_col, axis=1)

In [89]:
RFS.profile_report()

Summarize dataset:   0%|          | 0/17 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]